In [1]:
import random
import numpy as np
import tensorflow as tf
import keras
from keras.models import Sequential,Model
from keras.layers import Dense,Activation,Dropout,Input, BatchNormalization
from keras.optimizers import Adam
import matplotlib.pyplot as plt
import warnings
warnings.filterwarnings("ignore")
from sklearn.metrics import mean_squared_error
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import RobustScaler
from sklearn.model_selection import train_test_split

Using TensorFlow backend.


In [2]:
#--matplotlib
import matplotlib
matplotlib.use('Agg')
#matplotlib.rcParams['text.latex.preamble']=[r"\usepackage{amsmath}"]
#matplotlib.rc('text',usetex=True)
from matplotlib.backends.backend_pdf import PdfPages
from matplotlib.lines import Line2D
import pylab as py


import os
import pylab as py

from tools.tools import checkdir

# Generating the Models

In [3]:
path2nptabs='nptabs/'
path2nnmodels='nnmodels/'

In [4]:
def get_data(k,channel,flavor,path2nptabs,original=False):
    data=np.load('%s/%s/%s/%s.npy'%(path2nptabs,k,channel,flavor))

    num_inputs=3
    num_outputs=2
    #--split into input (x) and output (y)
    x=data[:num_inputs]
    y=data[num_inputs:]

    x,y=x.T,y.T
    x_train_orig,x_test,y_train_orig,y_test=train_test_split(x,y,test_size=0.2,random_state=0)
    xsc=MinMaxScaler()
    ysc=MinMaxScaler()
    x_train=xsc.fit_transform(x_train_orig)
    x_test=xsc.transform(x_test)
    y_train=ysc.fit_transform(y_train_orig)
    y_test=ysc.transform(y_test)

    if original: return x_train,x_test,y_train,y_test,x_train_orig,y_train_orig
    else: return x_train,x_test,y_train,y_test

In [5]:
def gen_model(EPOCHS, BATCH_SIZE, lr, k, channel, flavor, path2nptabs, path2nnmodels):

    print('\ngenerating model for %s, %s'%(channel,flavor))

    x_train,x_test,y_train,y_test,x_train_orig,y_train_orig = get_data(k,channel,flavor,path2nptabs,original=True)

    input=Input(shape= x_train[0].shape)
    x=Dense(120, activation='relu')(input)
    x = Dropout(0.01)(x)
    x=Dense(120, activation='relu')(x)
    x = Dropout(0.01)(x)
    x=Dense(120, activation='relu')(x)
    x = Dropout(0.01)(x)
    output=Dense(2)(x)
    model=Model(input,output)
    model.summary()
    model_optimizer=Adam(lr=lr, beta_1=0.9, beta_2=0.999, epsilon=1e-08, decay=0.00001) 
    model.compile(optimizer=model_optimizer,loss='mean_squared_error',metrics=['accuracy'])
    history = model.fit(x_train, y_train, batch_size=BATCH_SIZE, epochs=EPOCHS, validation_split=0.2, verbose=1)

    checkdir('%s/%s/%s'%(path2nnmodels,k,channel))
    filename='%s/%s/%s/%s'%(path2nnmodels,k,channel,flavor)
    np.save(filename,{'model':model,'history':history,'x_train_orig':x_train_orig,'y_train_orig':y_train_orig})

In [10]:
def plot_metrics(path2nnmodels,k,channel,flavor):
    checkdir('%s/%s/%s'%(path2nnmodels,k,channel))
    modeldata=np.load('%s/%s/%s/%s.npy'%(path2nnmodels,k,channel,flavor),allow_pickle=True)[()]

    model,history=modeldata['model'],modeldata['history']

    nrows, ncols = 1, 2
    fig=plt.figure(figsize=(ncols*7,nrows*4))
    ax1=plt.subplot(nrows, ncols, 1)
    ax2=plt.subplot(nrows, ncols, 2)

    ax1.semilogy()

    ax1.plot(history.history['loss'])
    ax1.plot(history.history['val_loss'])
    ax1.set_ylabel('loss')
    ax1.set_xlabel('epoch')
    ax1.legend(['train','validation'], loc='upper left')

    ax2.plot(history.history['accuracy'])
    ax2.plot(history.history['val_accuracy'])
    ax2.set_ylabel('accuracy')
    ax2.set_xlabel('epoch')
    ax2.legend(['train','validation'], loc='upper left')

    plt.tight_layout()
    checkdir('gallery/%s/%s/%s'%(k,channel,flavor))
    filename='gallery/%s/%s/%s/metrics.png'%(k,channel,flavor)
    plt.savefig(filename)
    plt.close()
    print('Saving figure to %s'%filename)


In [7]:
def plot_predictions(path2nnmodels,k,channel,flavor,path2nptabs):
 
    x_train,x_test,y_train,y_test= get_data(k,channel,flavor,path2nptabs)

    y_test=y_test.T
    y_train=y_train.T

    #--load model data
    modeldata=np.load('%s/%s/%s/%s.npy'%(path2nnmodels,k,channel,flavor),allow_pickle=True)[()]
    model = modeldata['model']

    y_pred=model.predict(x_test).T

    nrows, ncols = 1, 2
    fig=plt.figure(figsize=(ncols*7,nrows*4))
    ax1=plt.subplot(nrows, ncols, 1)
    ax2=plt.subplot(nrows, ncols, 2)

    ax1.scatter(y_test[0],y_pred[0],label='Predicted',s=0.5)
    ax1.plot(y_test[0], y_test[0], color='orange')
    ax1.legend()
    ax1.set_xlabel('Re($\sigma$)_test')
    ax1.set_ylabel('Re($\sigma$)_pred')

    ax2.scatter(y_test[1],y_pred[1],label='Predicted',s=0.5)
    ax2.plot(y_test[1], y_test[1], color='orange')
    ax2.legend()
    ax2.set_xlabel('Im($\sigma$)_test')
    ax2.set_ylabel('Im($\sigma$)_pred')
    checkdir('gallery/%s/%s/%s'%(k,channel,flavor))
    filename='gallery/%s/%s/%s/predictions.png'%(k,channel,flavor)
    plt.savefig(filename)
    plt.close()
    print('Saving figure to %s'%filename)


    y_pred=model.predict(x_train).T

    nrows, ncols = 1, 2
    fig=plt.figure(figsize=(ncols*7,nrows*4))
    ax1=plt.subplot(nrows, ncols, 1)
    ax2=plt.subplot(nrows, ncols, 2)

    ax1.scatter(y_train[0],y_pred[0],label='Predicted',s=0.5)
    ax1.plot(y_train[0], y_train[0], color='orange')
    ax1.legend()
    ax1.set_xlabel('Re($\sigma$)_train')
    ax1.set_ylabel('Re($\sigma$)_pred')

    ax2.scatter(y_train[1],y_pred[1],label='Predicted',s=0.5)
    ax2.plot(y_train[1], y_train[1], color='orange')
    ax2.legend()
    ax2.set_xlabel('Im($\sigma$)_train')
    ax2.set_ylabel('Im($\sigma$)_pred')
    checkdir('gallery/%s/%s/%s'%(k,channel,flavor))
    filename='gallery/%s/%s/%s/trainingset.png'%(k,channel,flavor)
    plt.savefig(filename)
    plt.close()
    print('Saving figure to %s'%filename)

In [9]:
#--generate the model for 30001
k=30001
epochs=1000

channel='qA,qbB'
for flav in ['ub','db','sb','cb','bb']:
    gen_model(epochs,32,1e-4,k,channel,flav,path2nptabs,path2nnmodels)
    plot_metrics(path2nnmodels,k,channel,flav)
    plot_predictions(path2nnmodels,k,channel,flav,path2nptabs)
channel='qbA,qB'
for flav in ['u','d','s','c','b']:
    gen_model(epochs,32,1e-4,k,channel,flav,path2nptabs,path2nnmodels)
    plot_metrics(path2nnmodels,k,channel,flav)
    plot_predictions(path2nnmodels,k,channel,flav,path2nptabs)
channel='qA,gB'
for flav in ['g']:
    gen_model(epochs,32,1e-4,k,channel,flav,path2nptabs,path2nnmodels)
    plot_metrics(path2nnmodels,k,channel,flav)
    plot_predictions(path2nnmodels,k,channel,flav,path2nptabs)
channel='gA,qB'
for flav in ['u','d','s','c','b','ub','db','sb','cb','bb']:
    gen_model(epochs,32,1e-4,k,channel,flav,path2nptabs,path2nnmodels)
    plot_metrics(path2nnmodels,k,channel,flav)
    plot_predictions(path2nnmodels,k,channel,flav,path2nptabs)


generating model for qA,qbB, ub
Model: "model_2"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         (None, 3)                 0         
_________________________________________________________________
dense_5 (Dense)              (None, 120)               480       
_________________________________________________________________
dropout_4 (Dropout)          (None, 120)               0         
_________________________________________________________________
dense_6 (Dense)              (None, 120)               14520     
_________________________________________________________________
dropout_5 (Dropout)          (None, 120)               0         
_________________________________________________________________
dense_7 (Dense)              (None, 120)               14520     
_________________________________________________________________
dropout_6 (Dropout)       

Epoch 47/1000
391/391 [==============================] - 0s 50us/step - loss: 0.0331 - accuracy: 0.7954 - val_loss: 0.0267 - val_accuracy: 0.8061
Epoch 48/1000
391/391 [==============================] - 0s 56us/step - loss: 0.0333 - accuracy: 0.7903 - val_loss: 0.0264 - val_accuracy: 0.8061
Epoch 49/1000
391/391 [==============================] - 0s 56us/step - loss: 0.0323 - accuracy: 0.8005 - val_loss: 0.0264 - val_accuracy: 0.8673
Epoch 50/1000
391/391 [==============================] - 0s 56us/step - loss: 0.0331 - accuracy: 0.8210 - val_loss: 0.0261 - val_accuracy: 0.8061
Epoch 51/1000
391/391 [==============================] - 0s 53us/step - loss: 0.0332 - accuracy: 0.7801 - val_loss: 0.0259 - val_accuracy: 0.8061
Epoch 52/1000
391/391 [==============================] - 0s 55us/step - loss: 0.0322 - accuracy: 0.8005 - val_loss: 0.0257 - val_accuracy: 0.8673
Epoch 53/1000
391/391 [==============================] - 0s 57us/step - loss: 0.0324 - accuracy: 0.8184 - val_loss: 0.0255 -

391/391 [==============================] - 0s 58us/step - loss: 0.0239 - accuracy: 0.8798 - val_loss: 0.0168 - val_accuracy: 0.9286
Epoch 104/1000
391/391 [==============================] - 0s 56us/step - loss: 0.0240 - accuracy: 0.8875 - val_loss: 0.0166 - val_accuracy: 0.9286
Epoch 105/1000
391/391 [==============================] - 0s 51us/step - loss: 0.0237 - accuracy: 0.8747 - val_loss: 0.0164 - val_accuracy: 0.9286
Epoch 106/1000
391/391 [==============================] - 0s 56us/step - loss: 0.0236 - accuracy: 0.8747 - val_loss: 0.0164 - val_accuracy: 0.9286
Epoch 107/1000
391/391 [==============================] - 0s 60us/step - loss: 0.0236 - accuracy: 0.8849 - val_loss: 0.0162 - val_accuracy: 0.9286
Epoch 108/1000
391/391 [==============================] - 0s 55us/step - loss: 0.0231 - accuracy: 0.8798 - val_loss: 0.0160 - val_accuracy: 0.9388
Epoch 109/1000
391/391 [==============================] - 0s 54us/step - loss: 0.0228 - accuracy: 0.8977 - val_loss: 0.0158 - val_acc

Epoch 159/1000
391/391 [==============================] - 0s 51us/step - loss: 0.0155 - accuracy: 0.9156 - val_loss: 0.0099 - val_accuracy: 0.9694
Epoch 160/1000
391/391 [==============================] - 0s 61us/step - loss: 0.0154 - accuracy: 0.9207 - val_loss: 0.0098 - val_accuracy: 0.9796
Epoch 161/1000
391/391 [==============================] - 0s 56us/step - loss: 0.0157 - accuracy: 0.9258 - val_loss: 0.0098 - val_accuracy: 0.9694
Epoch 162/1000
391/391 [==============================] - 0s 56us/step - loss: 0.0150 - accuracy: 0.9284 - val_loss: 0.0096 - val_accuracy: 0.9694
Epoch 163/1000
391/391 [==============================] - 0s 55us/step - loss: 0.0145 - accuracy: 0.9130 - val_loss: 0.0095 - val_accuracy: 0.9796
Epoch 164/1000
391/391 [==============================] - 0s 57us/step - loss: 0.0148 - accuracy: 0.9258 - val_loss: 0.0095 - val_accuracy: 0.9490
Epoch 165/1000
391/391 [==============================] - 0s 56us/step - loss: 0.0144 - accuracy: 0.9335 - val_loss: 0

Epoch 215/1000
391/391 [==============================] - 0s 59us/step - loss: 0.0102 - accuracy: 0.9233 - val_loss: 0.0062 - val_accuracy: 0.9694
Epoch 216/1000
391/391 [==============================] - 0s 58us/step - loss: 0.0101 - accuracy: 0.9258 - val_loss: 0.0058 - val_accuracy: 0.9796
Epoch 217/1000
391/391 [==============================] - 0s 66us/step - loss: 0.0102 - accuracy: 0.9386 - val_loss: 0.0056 - val_accuracy: 0.9796
Epoch 218/1000
391/391 [==============================] - 0s 66us/step - loss: 0.0097 - accuracy: 0.9361 - val_loss: 0.0056 - val_accuracy: 0.9796
Epoch 219/1000
391/391 [==============================] - 0s 55us/step - loss: 0.0095 - accuracy: 0.9565 - val_loss: 0.0055 - val_accuracy: 0.9898
Epoch 220/1000
391/391 [==============================] - 0s 54us/step - loss: 0.0095 - accuracy: 0.9386 - val_loss: 0.0055 - val_accuracy: 0.9796
Epoch 221/1000
391/391 [==============================] - 0s 56us/step - loss: 0.0097 - accuracy: 0.9463 - val_loss: 0

...

Epoch 830/1000
391/391 [==============================] - 0s 57us/step - loss: 0.0048 - accuracy: 0.8696 - val_loss: 0.0045 - val_accuracy: 0.8265
Epoch 831/1000
391/391 [==============================] - 0s 56us/step - loss: 0.0050 - accuracy: 0.8593 - val_loss: 0.0046 - val_accuracy: 0.8265
Epoch 832/1000
391/391 [==============================] - 0s 54us/step - loss: 0.0046 - accuracy: 0.8645 - val_loss: 0.0045 - val_accuracy: 0.8061
Epoch 833/1000
391/391 [==============================] - 0s 54us/step - loss: 0.0047 - accuracy: 0.8696 - val_loss: 0.0045 - val_accuracy: 0.8061
Epoch 834/1000
391/391 [==============================] - 0s 56us/step - loss: 0.0055 - accuracy: 0.8440 - val_loss: 0.0048 - val_accuracy: 0.7959
Epoch 835/1000
391/391 [==============================] - 0s 56us/step - loss: 0.0043 - accuracy: 0.8824 - val_loss: 0.0045 - val_accuracy: 0.8163
Epoch 836/1000
391/391 [==============================] - 0s 53us/step - loss: 0.0051 - accuracy: 0.8542 - val_loss: 0

Epoch 886/1000
391/391 [==============================] - 0s 50us/step - loss: 0.0041 - accuracy: 0.8619 - val_loss: 0.0043 - val_accuracy: 0.8571
Epoch 887/1000
391/391 [==============================] - 0s 59us/step - loss: 0.0044 - accuracy: 0.8593 - val_loss: 0.0040 - val_accuracy: 0.8367
Epoch 888/1000
391/391 [==============================] - 0s 53us/step - loss: 0.0044 - accuracy: 0.8645 - val_loss: 0.0041 - val_accuracy: 0.8265
Epoch 889/1000
391/391 [==============================] - 0s 53us/step - loss: 0.0048 - accuracy: 0.8721 - val_loss: 0.0041 - val_accuracy: 0.8265
Epoch 890/1000
391/391 [==============================] - 0s 56us/step - loss: 0.0044 - accuracy: 0.8747 - val_loss: 0.0042 - val_accuracy: 0.8265
Epoch 891/1000
391/391 [==============================] - 0s 53us/step - loss: 0.0046 - accuracy: 0.8696 - val_loss: 0.0041 - val_accuracy: 0.8367
Epoch 892/1000
391/391 [==============================] - 0s 54us/step - loss: 0.0045 - accuracy: 0.8670 - val_loss: 0

Epoch 942/1000
391/391 [==============================] - 0s 52us/step - loss: 0.0046 - accuracy: 0.8593 - val_loss: 0.0038 - val_accuracy: 0.8469
Epoch 943/1000
391/391 [==============================] - 0s 58us/step - loss: 0.0042 - accuracy: 0.8645 - val_loss: 0.0039 - val_accuracy: 0.8469
Epoch 944/1000
391/391 [==============================] - 0s 50us/step - loss: 0.0038 - accuracy: 0.9003 - val_loss: 0.0039 - val_accuracy: 0.8367
Epoch 945/1000
391/391 [==============================] - 0s 52us/step - loss: 0.0040 - accuracy: 0.8721 - val_loss: 0.0038 - val_accuracy: 0.8265
Epoch 946/1000
391/391 [==============================] - 0s 57us/step - loss: 0.0039 - accuracy: 0.8849 - val_loss: 0.0039 - val_accuracy: 0.8265
Epoch 947/1000
391/391 [==============================] - 0s 52us/step - loss: 0.0045 - accuracy: 0.8619 - val_loss: 0.0039 - val_accuracy: 0.8265
Epoch 948/1000
391/391 [==============================] - 0s 52us/step - loss: 0.0046 - accuracy: 0.8721 - val_loss: 0

Epoch 998/1000
391/391 [==============================] - 0s 59us/step - loss: 0.0044 - accuracy: 0.8568 - val_loss: 0.0033 - val_accuracy: 0.8469
Epoch 999/1000
391/391 [==============================] - 0s 51us/step - loss: 0.0039 - accuracy: 0.8951 - val_loss: 0.0036 - val_accuracy: 0.8367
Epoch 1000/1000
391/391 [==============================] - 0s 57us/step - loss: 0.0037 - accuracy: 0.8670 - val_loss: 0.0033 - val_accuracy: 0.8367
{'model': <keras.engine.training.Model object at 0x14d064590>, 'history': <keras.callbacks.callbacks.History object at 0x14d62dfd0>, 'x_train_orig': array([[  0.35      ,   0.38962528,   1.51037472],
       [  0.05      , -20.3837469 ,  22.2837469 ],
       [  0.05      ,   1.16343578,   0.73656422],
       ...,
       [  0.25      ,   0.79808659,   1.10191341],
       [  0.45      , -21.12018282,  23.02018282],
       [  0.55      ,   1.21253151,   0.68746849]]), 'y_train_orig': array([[-6.59011174e-11, -5.71524615e-11],
       [ 5.23589898e-12,  1.03

Saving figure to gallery/30001/gA,qB/bb/metrics.png
Saving figure to gallery/30001/gA,qB/bb/predictions.png
Saving figure to gallery/30001/gA,qB/bb/trainingset.png


# Comparing with actual cross-sections

In [11]:
#--from tools
from tools.config import conf,load_config
from tools import reader

#--from qcdlib
from qcdlib import aux,eweak,alphaS,mellin

#--from dy
from dy import theory,reader,fakepdf

In [12]:
conf['order']='NLO'
conf['aux']=aux.AUX()
conf['Q20']=conf['aux'].mc2
conf['eweak']=eweak.EWEAK()
conf['alphaS']=alphaS.ALPHAS()
conf['mellin-pion']=mellin.MELLIN(npts=4)
conf['mellin']=conf['mellin-pion']

conf['pdfA']=fakepdf.FAKEPDF()
conf['pdf-pion']=conf['pdfA']
conf['pdfB']=fakepdf.FAKEPDF()

In [13]:
conf['datasets']={}
conf['datasets']['dy-pion']={}
conf['datasets']['dy-pion']['filters']=[]
conf['datasets']['dy-pion']['filters'].append("Q2>4.16**2")
conf['datasets']['dy-pion']['filters'].append("Q2<8.34**2")
conf['datasets']['dy-pion']['filters'].append("xF>0")
conf['datasets']['dy-pion']['filters'].append("xF<0.9")
conf['datasets']['dy-pion']['xlsx']={}
conf['datasets']['dy-pion']['xlsx'][30001]='30001.xlsx'

conf['dy-pion tabs']=reader.READER().load_data_sets('dy-pion')
conf['path2ml4jam']='./'

loading dy-pion data sets 30001


In [14]:
conf['dy-pion']=theory.DY_PION()

conf['path2dytab-hybrid']='melltabs/'
conf['path2nntabs']='nnmodels/'

In [15]:
def get_xspace(k,part,flav=None):
    xspace=np.zeros(len(conf['dy-pion tabs'][k]['idx']))
    for i in range(len(xspace)):
        Q2   = conf['dy-pion tabs'][k]['Q2'][i]
        Jac  = conf['dy-pion tabs'][k]['Jac'][i]
        units= conf['dy-pion tabs'][k]['Units'][i]
        S    = conf['dy-pion tabs'][k]['S'][i]
        Y    = conf['dy-pion tabs'][k]['Y'][i]
        if part!='full': xspace[i]=conf['dy-pion'].get_xsec(Q2,S,Y,Q2,ilum='flavors',part=part,flav=flav) * Jac * units
        elif part=='full': xspace[i]=conf['dy-pion'].get_xsec(Q2,S,Y,Q2,ilum='normal',part=part,flav=flav) * Jac * units
    return xspace

def get_mellspace(k,part,flav=None):
    conf['dy-pion'].load_melltab_hybrid()
    mellspace=np.zeros(len(conf['dy-pion tabs'][k]['idx']))
    for i in range(len(mellspace)):
        Q2   = conf['dy-pion tabs'][k]['Q2'][i]
        Jac  = conf['dy-pion tabs'][k]['Jac'][i]
        units= conf['dy-pion tabs'][k]['Units'][i]
        mellspace[i]=conf['dy-pion'].get_xsec_mell_hybrid(k,i,Q2,part,flav=flav) * Jac * units
    return mellspace

def get_nnspace(k,part,flav=None):
    conf['dy-pion'].load_nn_hybrid()
    nnspace=np.zeros(len(conf['dy-pion tabs'][k]['idx']))
    for i in range(len(nnspace)):
        Q2   = conf['dy-pion tabs'][k]['Q2'][i]
        Jac  = conf['dy-pion tabs'][k]['Jac'][i]
        units= conf['dy-pion tabs'][k]['Units'][i]
        nnspace[i]=conf['dy-pion'].get_xsec_mell_hybrid_nn(k,i,Q2,part,flav=flav) * Jac * units
    return nnspace

In [16]:
def plot_mellin(mell,nn,k,part,flav,i):
    Z=conf['mellin'].Z
    nrows,ncols=1,2
    fig=py.figure(figsize=(4*ncols,4*nrows))

    ax=py.subplot(nrows,ncols,1)
    ax.plot(Z,mell.real,label='mellin')
    ax.plot(Z,nn.real,label='nn')
    ax.set_title(r'$x_F=%.3f$'%conf['dy-pion tabs'][k]['xF'][i],size=20)
    ax.set_xlabel(r'$Z$')
    ax.set_ylabel(r'Re[$\sigma$]')

    ax=py.subplot(nrows,ncols,2)
    ax.plot(Z,mell.imag,label='mellin')
    ax.plot(Z,nn.imag,label='nn')
    ax.set_title(r'$Q^2=%.3f$'%conf['dy-pion tabs'][k]['Q2'][i],size=20)
    ax.set_xlabel(r'$Z$')
    ax.set_ylabel(r'Im[$\sigma$]')

    ax.legend()

    py.tight_layout()
    if part=='full':
        checkdir('gallery/%s/%s'%(k,part))
        py.savefig('gallery/%s/%s/testmell%s.png'%(k,part,i))
        py.close()
    else:
        checkdir('gallery/%s/%s/%s'%(k,part,flav))
        py.savefig('gallery/%s/%s/%s/testmell%s.png'%(k,part,flav,i))
        py.close()

In [17]:
def plot(tabs,x,mell,nn,k,part,flav):

    nrows,ncols=1,1
    fig=py.figure(figsize=(ncols*5,nrows*7))
    ax=py.subplot(nrows,ncols,1)

    xF=conf['dy-pion tabs'][k]['xF']
    
    ax.plot(xF,x,label='x-space')
    ax.plot(xF,mell,'*',label='using Mellin tables')
    ax.plot(xF,nn,label='neural net')
    ax.legend()

    ax.set_ylabel(r'$\frac{d\sigma}{dx_F d\sqrt{\tau}}$')
    ax.set_xlabel(r'$x_F$')
    ax.set_title(r'dataset=%s'%k)

    py.tight_layout()
    if part=='full':
        checkdir('gallery/%s/%s'%(k,part))
        py.savefig('gallery/%s/%s/test.png'%(k,part))
        py.close()
    else:
        checkdir('gallery/%s/%s/%s'%(k,part,flav))
        py.savefig('gallery/%s/%s/%s/test.png'%(k,part,flav))
        py.close()

In [ ]:
k=30001
parts=['qA,qbB','qbA,qB','qA,gB','gA,qB']
for part in parts:
    if part=='qA,qbB': flavs=['ub','db','sb','cb','bb']
    if part=='qbA,qB': flavs=['u','d','s','c','b']
    if part=='qA,gB':  flavs=['g']
    if part=='gA,qB':  flavs=['u','ub','d','db','s','sb','c','cb','b','bb']
    for f in flavs:
        xspacedat=get_xspace(k,part,flav=f)
        mellspacedat=get_mellspace(k,part,flav=f)
        nnspacedat=get_nnspace(k,part,flav=f)

        plot(conf['dy-pion tabs'][k],xspacedat,mellspacedat,nnspacedat,k,part,f)
        for i in range(len(conf['dy-pion tabs'][k]['idx'])):
            mellinxsec=np.load('%s/data/%s/%s/%s/%smell.npy'%(conf['path2ml4jam'],k,part,f,i),allow_pickle=True)[()]
            nnxsec=np.load('%s/data/%s/%s/%s/%snn.npy'%(conf['path2ml4jam'],k,part,f,i),allow_pickle=True)[()]

            plot_mellin(mellinxsec,nnxsec,k,part,f,i)
part='full'
xspacedat=get_xspace(k,part)
mellspacedat=get_mellspace(k,part)
nnspacedat=get_nnspace(k,part)

plot(conf['dy-pion tabs'][k],xspacedat,mellspacedat,nnspacedat,k,part,None)

for i in range(len(conf['dy-pion tabs'][k]['idx'])):
    mellinub=np.load('%s/data/%s/%s/%sxsecmell.npy'%(conf['path2ml4jam'],k,part,i),allow_pickle=True)[()]
    nnub=np.load('%s/data/%s/%s/%sxsecnn.npy'%(conf['path2ml4jam'],k,part,i),allow_pickle=True)[()]

    plot_mellin(mellinub,nnub,k,part,None,i)